In [2]:
#Libraries
import pandas as pd
import json
from classified_names import output
import re
from geopy.geocoders import ArcGIS
from geopy.exc import GeocoderTimedOut

In [3]:
#Opening file
with open('SPYUR.company_info.json', 'r') as file:
    spyur_data = json.load(file)  

In [4]:
spyur_data

[{'_id': {'$oid': '667a2ff845687da4e35a4aa0'},
  'Company Name': 'SPYUR INFORMATION SYSTEM Limited Liability Company (LLC)',
  'Executive': ['Ashot K. Grigoryan, Founding Director',
   'Ani Melikyan, Head of Marketing Department'],
  'Address': 'Armenia, 0028, YerevanKievyan St., 5/4 Building',
  'Phone Numbers': '113, +374-10-519999, +374-11-331331, +374-60-519999, +1-747-2281111(USA)',
  'Site URLs': ['https://spyur.am',
   'http://yellowpages.am',
   'http://b2b.am',
   'http://kompass.am'],
  'Web Links': ['https://spyur.am/spyur',
   'https://www.facebook.com/spyuram',
   'https://www.instagram.com/spyurinformationsystem',
   'https://www.youtube.com/user/ArmenianCompanies',
   'https://www.linkedin.com/company/spyur-information-center',
   'https://twitter.com/spyuram',
   'https://t.me/spyur',
   'https://www.pinterest.com/spyur_information_system/_saved',
   'https://spyur.am/spyur'],
  'Number of employees': 'From 51 to 250',
  'Form of ownership': 'Non-governmental',
  'Year 

In [5]:
#Converting to DataFrame, removing multiple exacutive companies 
spyur_df = pd.DataFrame(spyur_data)


In [85]:
#Extracting only full names from Exacutives column, finding first names, last names
names = spyur_df['Executive'].apply(lambda x: [entry.split(',')[0] for entry in x])
def extract_names(name_lists, suffixes=["yan", "ian", 'ts', 'unc', 'jan', 'tz', 'ians']):
    last_names = []
    middle_names = []
    first_names = []

    for name_list in name_lists:
        if name_list:
            full_name = name_list[0]
            name_parts = full_name.split()
            current_first_names = []

            for part in name_parts:
                if part.endswith('.'):
                    middle_names.append(part)
                elif any(part.endswith(suffix) for suffix in suffixes):
                    last_names.append(part)
                else:
                    current_first_names.append(part)

            first_names.append(current_first_names)

    return last_names, middle_names, first_names
last_names, middle_names, first_names = extract_names(names)

In [86]:
len(first_names)

13636

In [ ]:
#Adding First_names column to DataFrame, removing multiple name rows (non armenian), converting names from lists to strings(for mapping), adding Gender column by mapping with openai api output
spyur_df['First names'] = first_names
spyur_df = spyur_df[spyur_df['First names'].apply(lambda x: len(x)==1)]
spyur_df['First names'] = spyur_df['First names'].apply(lambda x: x[0] if isinstance(x, list) and len(x) > 0 else None)
spyur_df['Gender'] = spyur_df['First names'].map(output)



In [99]:
#Removig Non-governmental companies from Russia
spyur_df = spyur_df[spyur_df['Form of ownership']!= 'Non-governmental (from Russia)']

In [89]:
#Finding the last number from Number of Employees and adding column Company Size,changing NaN values, changing Year established type
def extract_last_number(s):
    if pd.isna(s):
        return s
    match = re.search(r'(\d+)(?!.*\d)', s)
    return int(match.group(1)) if match else None
spyur_df['Company Size'] = spyur_df['Number of employees'].apply(extract_last_number)
# avg_size = spyur_df['Company Size'].mean()
# spyur_df['Company Size'] = spyur_df['Company Size'].fillna(round(avg_size))
mode = spyur_df['Company Size'].mode()[0]
spyur_df['Company Size'] = spyur_df['Company Size'].fillna(mode)
spyur_df['Year established'] = spyur_df['Year established'].fillna(1990).astype('int')


In [91]:
spyur_df

_id  \
1      {'$oid': '667a2ff845687da4e35a4aa1'}   
2      {'$oid': '667a2ff845687da4e35a4aa2'}   
3      {'$oid': '667a2ff945687da4e35a4aa3'}   
4      {'$oid': '667a2ffa45687da4e35a4aa4'}   
5      {'$oid': '667a2ffb45687da4e35a4aa5'}   
...                                     ...   
22916  {'$oid': '6681061729d5b70223ca5f6e'}   
22917  {'$oid': '6681061729d5b70223ca5f6f'}   
22918  {'$oid': '6681061729d5b70223ca5f70'}   
22919  {'$oid': '6681061729d5b70223ca5f71'}   
22920  {'$oid': '6681061829d5b70223ca5f72'}   

                                            Company Name  \
1      KOMPASS ARMENIA, REPRESENTATIVE OF KOMPASS.COM...   
2                   SUN PRINT INNOVATIVE PRINTING CENTER   
3      MIG TRANS INTERNATIONAL CARGO TRANSPORTATION C...   
4             VIAR GROUP Limited Liability Company (LLC)   
5                             HAPPY PRINT PRINTING HOUSE   
...                                                  ...   
22916                         HAPPY PRINT PRINTING HOUSE   
22917                           TPARAN AM PRINTING HOUSE   
22918                            HAF-HAF PET CHAIN STORE   
22919                           PRINT BOX PRINTING HOUSE   
22920  YEREVAN-AUDIT CONSULT Closed Joint-Stock Compa...   

                                      Executive  \
1                [Ashot K. Grigoryan, Director]   
2                  [Sergey Vardanyan, Director]   
3      [Inga G. Martirosyan, Founding Director]   
4                [Vitaly R. Sahakyan, Director]   
5                   [Maria Hovsepyan, Director]   
...                                         ...   
22916               [Maria Hovsepyan, Director]   
22917      [Vahe Zakaryan, Commercial Director]   
22918           [Maria R. Tsharakyan, Director]   
22919             [Edgar V. Umbreyan, Director]   
22920              [Levon K. Ghonyan, Director]   

                                                 Address  \
1        Armenia, 0028, YerevanKievyan St., 5/4 Building   
2      Armenia, 0051, YerevanGriboyedovi St., 60 Buil...   
3      Armenia, 0012, YerevanKomitasi Ave., 7/1 Building   
4      Armenia, 0014, YerevanAzatutyan Ave., 24/1 Bui...   
5      Armenia, 0026, YerevanArshakunyats Ave., 39/9 ...   
...                                                  ...   
22916  Armenia, 0026, YerevanArshakunyats Ave., 39/9 ...   
22917  Armenia, 0023, YerevanArshakunyats Ave., 4 Bui...   
22918  Armenia, 0033, YerevanMarshal Baghramyan Ave.,...   
22919  Armenia, 0023, YerevanArshakunyats Ave., 5 Bui...   
22920  Armenia, 0028, YerevanOrbeli Yeghbayrneri St.,...   

                                           Phone Numbers  \
1                                     +374-60-619999,424   
2      +374-96-477417(mobile), +374-96-977467(mobile)...   
3      +374-99-666179(mobile), +374-93-179666(mobile)...   
4                                 +374-94-070202(mobile)   
5      +374-41-577778(mobile), +374-93-258369(mobile)...   
...                                                  ...   
22916  +374-41-577778(mobile), +374-93-258369(mobile)...   
22917  +374-91-407038(mobile), +374-60-446685, +374-9...   
22918                             +374-98-423423(mobile)   
22919     +374-93-939592(mobile), +374-99-939592(mobile)   
22920             +374-11-300331, +374-93-250580(mobile)   

                          Site URLs  \
1               [http://kompass.am]   
2          [http://www.sunprint.am]   
3                                []   
4                                []   
5                                []   
...                             ...   
22916                            []   
22917        [http://www.tparan.am]   
22918       [http://www.haf-haf.am]   
22919      [http://www.printbox.am]   
22920  [http://www.yerevanaudit.am]   

                                               Web Links Number of employees  \
1      [https://spyur.am/kompass, https://spyur.am/ko...       From 16 to 50   
2      [https://spyur.am/sunprint, https://www.facebo...            Up

In [97]:
# Function to geocode addresses and return (latitude, longitude)
def geocode_address(address):
    geolocator = ArcGIS(timeout=10)
    try:
        location = geolocator.geocode(address)
        if location:
            return location.latitude, location.longitude
        else:
            return None, None
    except GeocoderTimedOut:
        return None, None
    except Exception as e:
        print(f"Error geocoding address '{address}': {e}")
        return None, None

In [100]:
# Applying geocoding to each row in the DataFrame and create 'Location' column
locations = []
for index, row in spyur_df.iterrows():
    address = row['Address']
    lat, lon = geocode_address(address)
    locations.append((lat, lon))
    print(f'Added location {lat}, {lon}')
print('Geocoding is comleted')

Added location 40.192831992261, 44.485009016695
Added location 40.213345987822, 44.515337005498
Added location 40.202862992977, 44.496777963125
Added location 40.209590015099, 44.530592991286
Added location 40.157032003699, 44.502172975103
Added location 40.293084855, 44.940221311
Added location 40.197192006836, 44.492922958216
Added location 40.169381019738, 44.507850960134
Added location 40.293084855, 44.940221311
Added location 40.293084855, 44.940221311
Added location 40.157032003699, 44.502172975103
Added location 40.293084855, 44.940221311
Added location 40.293084855, 44.940221311
Added location 40.171136986544, 44.521081039925
Added location 40.293084855, 44.940221311
Added location 52.9883527, -1.987391
Added location 40.293084855, 44.940221311
Added location 40.14634599916, 44.510768030077
Added location 40.293084855, 44.940221311
Added location 40.201441003103, 44.550127016637
Added location 40.222281794651, 44.491757542823
Added location 40.293084855, 44.940221311
Added loca

In [101]:
#Adding Location column to DataFrame
spyur_df['Location'] = locations

In [102]:
spyur_df

_id  \
1      {'$oid': '667a2ff845687da4e35a4aa1'}   
2      {'$oid': '667a2ff845687da4e35a4aa2'}   
3      {'$oid': '667a2ff945687da4e35a4aa3'}   
4      {'$oid': '667a2ffa45687da4e35a4aa4'}   
5      {'$oid': '667a2ffb45687da4e35a4aa5'}   
...                                     ...   
22916  {'$oid': '6681061729d5b70223ca5f6e'}   
22917  {'$oid': '6681061729d5b70223ca5f6f'}   
22918  {'$oid': '6681061729d5b70223ca5f70'}   
22919  {'$oid': '6681061729d5b70223ca5f71'}   
22920  {'$oid': '6681061829d5b70223ca5f72'}   

                                            Company Name  \
1      KOMPASS ARMENIA, REPRESENTATIVE OF KOMPASS.COM...   
2                   SUN PRINT INNOVATIVE PRINTING CENTER   
3      MIG TRANS INTERNATIONAL CARGO TRANSPORTATION C...   
4             VIAR GROUP Limited Liability Company (LLC)   
5                             HAPPY PRINT PRINTING HOUSE   
...                                                  ...   
22916                         HAPPY PRINT PRINTING HOUSE   
22917                           TPARAN AM PRINTING HOUSE   
22918                            HAF-HAF PET CHAIN STORE   
22919                           PRINT BOX PRINTING HOUSE   
22920  YEREVAN-AUDIT CONSULT Closed Joint-Stock Compa...   

                                      Executive  \
1                [Ashot K. Grigoryan, Director]   
2                  [Sergey Vardanyan, Director]   
3      [Inga G. Martirosyan, Founding Director]   
4                [Vitaly R. Sahakyan, Director]   
5                   [Maria Hovsepyan, Director]   
...                                         ...   
22916               [Maria Hovsepyan, Director]   
22917      [Vahe Zakaryan, Commercial Director]   
22918           [Maria R. Tsharakyan, Director]   
22919             [Edgar V. Umbreyan, Director]   
22920              [Levon K. Ghonyan, Director]   

                                                 Address  \
1        Armenia, 0028, YerevanKievyan St., 5/4 Building   
2      Armenia, 0051, YerevanGriboyedovi St., 60 Buil...   
3      Armenia, 0012, YerevanKomitasi Ave., 7/1 Building   
4      Armenia, 0014, YerevanAzatutyan Ave., 24/1 Bui...   
5      Armenia, 0026, YerevanArshakunyats Ave., 39/9 ...   
...                                                  ...   
22916  Armenia, 0026, YerevanArshakunyats Ave., 39/9 ...   
22917  Armenia, 0023, YerevanArshakunyats Ave., 4 Bui...   
22918  Armenia, 0033, YerevanMarshal Baghramyan Ave.,...   
22919  Armenia, 0023, YerevanArshakunyats Ave., 5 Bui...   
22920  Armenia, 0028, YerevanOrbeli Yeghbayrneri St.,...   

                                           Phone Numbers  \
1                                     +374-60-619999,424   
2      +374-96-477417(mobile), +374-96-977467(mobile)...   
3      +374-99-666179(mobile), +374-93-179666(mobile)...   
4                                 +374-94-070202(mobile)   
5      +374-41-577778(mobile), +374-93-258369(mobile)...   
...                                                  ...   
22916  +374-41-577778(mobile), +374-93-258369(mobile)...   
22917  +374-91-407038(mobile), +374-60-446685, +374-9...   
22918                             +374-98-423423(mobile)   
22919     +374-93-939592(mobile), +374-99-939592(mobile)   
22920             +374-11-300331, +374-93-250580(mobile)   

                          Site URLs  \
1               [http://kompass.am]   
2          [http://www.sunprint.am]   
3                                []   
4                                []   
5                                []   
...                             ...   
22916                            []   
22917        [http://www.tparan.am]   
22918       [http://www.haf-haf.am]   
22919      [http://www.printbox.am]   
22920  [http://www.yerevanaudit.am]   

                                               Web Links Number of employees  \
1      [https://spyur.am/kompass, https://spyur.am/ko...       From 16 to 50   
2      [https://spyur.am/sunprint, https://www.facebo...            Up

In [103]:
#Saving Dataframe as pkl file
spyur_df.to_pickle('spyur_df.pkl')